# Wintermute DeFi Exploratory Analysis

Quant Researcher Internship – Test Assignment  
Author: *Ismail Ouahchi*  
Date: April 2025

This notebook analyzes on chain transfers associated with Wintermute for a single day.  
The goals are:

- Identify all counterparties interacting with Wintermute  
- Classify them as DeFi, Non DeFi, Internal, or Unknown  
- Focus on DeFi only interactions  
- Analyze traded tokens, chains, DeFi protocols, and temporal patterns  
- Produce clear tables and visualizations to support a written summary


## 0. Setup


In [110]:
import pandas as pd
import numpy as np
import requests
import plotly.express as px
import plotly.graph_objects as go


pd.set_option("display.max_rows", 50)
pd.set_option("display.max_columns", 20)
pd.set_option("display.width", 120)


## 1. Data loading and basic inspection


In [65]:
# Path to the CSV file
# Adjust the path if the file is located elsewhere
csv_path = "wintermute_transfers_search_default_2025-04-08.csv"

df = pd.read_csv(csv_path)

# Parse timestamps
df["timestamp"] = pd.to_datetime(df["timestamp"])

df.head()


timestamp                                from_address        from_entity  \
0 2025-04-08 12:49:57+00:00  0xB1026b8e7276e7AC75410F1fcbbe21796e8f7526            Camelot   
1 2025-04-08 12:49:54+00:00  0xcDa53B1F66614552F834cEeF361A8D12a0B8DaD8            Uniswap   
2 2025-04-08 12:49:51+00:00  0xb2cc224c1c9feE385f8ad6a55b4d94E92359DC59  Aerodrome Finance   
3 2025-04-08 12:49:51+00:00  0x51C72848c68a965f66FA7a88855F9f7784502a7F         Wintermute   
4 2025-04-08 12:49:50+00:00  0x641C00A822e8b671738d32a431a4Fb6074E5c79d            Uniswap   

                                   to_address    to_entity token        value           usd  \
0  0x51C72848c68a965f66FA7a88855F9f7784502a7F   Wintermute  USDC   438.108563    438.108563   
1  0x51C72848c68a965f66FA7a88855F9f7784502a7F   Wintermute   ARB  3837.138536   1062.879700   
2  0x51C72848c68a965f66FA7a88855F9f7784502a7F   Wintermute  WETH     7.345922  11533.612401   
3  0x72AB388E2E2F6FaceF59E3C3FA2C4E29011c2D38  PancakeSwap  USDC  2143.712587   2143.712587   
4  0x51C72848c68a965f66FA7a88855F9f7784502a7F   Wintermute  WETH     0.470011    737.550466   

                                             tx_hash         chain  block_number  
0  0x98058c529466064c355bdfea3cfebe399344678f20bb...  arbitrum_one   324218955.0  
1  0x405b146ac6a52b93e5a77760a4b49a87015b5c5e0659...  arbitrum_one   324218945.0  
2  0x7f370fc61bed7241d846c4907a4e616e69ce60ff0192...          base    28663622.0  
3  0x88b4fb948e95cc2b9a22c48efe3d6a6788209302e72f...          base    28663622.0  
4  0x39fc603c882c2f5af51b7f8cfc8eb58753f5e42eff94...  arbitrum_one   324218918.0

In [66]:
# Basic shape and columns
df.shape, df.columns


((437000, 11),
 Index(['timestamp', 'from_address', 'from_entity', 'to_address', 'to_entity', 'token', 'value', 'usd', 'tx_hash',
        'chain', 'block_number'],
       dtype='object'))

**Notes**

- The dataset contains all transfers for a single day.  
- Columns include timestamp, from and to addresses, entities, token, USD value, transaction hash, chain, and block number.


## 2. Entity collection and overview


In [67]:
# Collect all unique entities from both sides
entities = pd.unique(pd.concat([df["from_entity"], df["to_entity"]], ignore_index=True))
entities = [e for e in entities if isinstance(e, str)]

len(entities)


85

In [68]:
# Take a quick look at some of the entities
sorted(entities)[:30]


['0x',
 '1inch',
 '@AnonPartTime',
 '@BinarySaga_',
 '@CipherCraze55',
 '@CipherNebulae',
 '@CryptoChamp87',
 '@IceSapp45',
 '@IshaanLlc',
 '@MatDefies',
 '@MrBigTimeCEO',
 '@NebulaVista99',
 '@RiceFarmerNFT',
 '@SolanaSeeker',
 '@SolsticeVault',
 '@TheCheckedBid33',
 '@TrueNFT33',
 '@Xaoxin_Ka',
 '@averagecontract',
 '@bitcocks',
 '@chris900eth',
 '@chuddybot',
 '@ec1ipse_sol',
 '@eiiriknft',
 '@glatebois',
 '@imCryptoGoku',
 '@inicola86',
 '@itzTenzy_',
 '@larutadeclau',
 '@quantumEVM18']

We will classify these entities using public DeFi protocol data from DeFiLlama and a set of heuristic rules for non DeFi entities such as centralized exchanges and wallets.


## 3. DeFiLlama protocol download and indexing

We use the public DeFiLlama API to get a list of known DeFi protocols.  
This lets us classify many entities in a systematic and reproducible way.


In [69]:
def load_defillama_protocols():
    """
    Fetch the protocol list from DeFiLlama.

    Endpoint: https://api.llama.fi/protocols
    
    Returns
    -------
    list of dict
        A list of protocol metadata entries.
    """
    url = "https://api.llama.fi/protocols"
    resp = requests.get(url, timeout=30)
    resp.raise_for_status()
    return resp.json()

try:
    protocols = load_defillama_protocols()
    print(f"Loaded {len(protocols)} protocols from DeFiLlama")
except Exception as e:
    print("Error loading DeFiLlama protocols:", e)
    protocols = []


Loaded 6731 protocols from DeFiLlama


In [70]:
def build_defillama_index(protocols):
    """
    Build lookup dictionaries by protocol name and symbol.
    Names and symbols are stored in lowercase for case insensitive matching.
    """
    by_name = {}
    by_symbol = {}
    
    for p in protocols:
        name = p.get("name")
        symbol = p.get("symbol")
        if isinstance(name, str):
            by_name[name.lower()] = p
        if isinstance(symbol, str):
            by_symbol[symbol.lower()] = p
    return by_name, by_symbol

defillama_by_name, defillama_by_symbol = build_defillama_index(protocols)
len(defillama_by_name), len(defillama_by_symbol)


(6731, 2873)

If DeFiLlama is not reachable, you can still proceed, but classification will fall back more heavily on heuristics.


## 4. Entity classification

We now define a classification function that assigns each entity to:

- "DeFi" with a protocol category from DeFiLlama when possible  
- "Non-DeFi" with a type (CEX, wallet, EOA) when identified by heuristics  
- "Internal" for Wintermute itself  
- "Unknown" for anything else


In [71]:
# Keywords to identify CEXes and wallet interfaces
CEX_KEYWORDS = [
    "binance", "coinbase", "kraken", "bybit", "okx",
    "bitstamp", "crypto.com", "bullish.com", "gate.io",
    "bitvavo", "backpack"
]

WALLET_KEYWORDS = [
    "metamask", "rainbow", "zerion"
]


In [72]:
def find_defillama_protocol(entity_name: str):
    """
    Try to resolve an entity name to a DeFiLlama protocol.

    Strategy:
    - exact name match
    - exact symbol match
    - simple substring match on name
    """
    if not isinstance(entity_name, str) or not protocols:
        return None
    
    key = entity_name.lower().strip()
    
    # 1) exact name match
    if key in defillama_by_name:
        return defillama_by_name[key]
    
    # 2) exact symbol match
    if key in defillama_by_symbol:
        return defillama_by_symbol[key]
    
    # 3) simple substring search
    for name_lower, p in defillama_by_name.items():
        if key in name_lower or name_lower in key:
            return p
    
    return None


In [73]:
def classify_non_defi(name: str):
    """
    Classify entities that are not recognized as DeFi protocols.

    Uses simple string based heuristics for:
    - centralized exchanges
    - wallet interfaces
    - social handles / EOAs
    """
    if not isinstance(name, str):
        return ("Unknown", "Unknown")
    
    lower = name.lower()
    
    # CEX classification
    if any(kw in lower for kw in CEX_KEYWORDS):
        return ("Non-DeFi", "CEX")
    
    # Wallet interfaces
    if any(kw in lower for kw in WALLET_KEYWORDS):
        return ("Non-DeFi", "Wallet / Interface")
    
    # Social handles and EOAs
    if lower.startswith("@"):
        return ("Non-DeFi", "EOA / Social handle")
    
    # Default
    return ("Unknown", "Unknown")


In [74]:
def classify_entity(name: str):
    """
    Classify a single entity into (group, type).

    group is one of: "DeFi", "Non-DeFi", "Internal", "Unknown"
    type is a more detailed string such as "Dexes", "Lending", "CEX", "Wallet", and so on.
    """
    # Special case for Wintermute itself
    if name == "Wintermute":
        return ("Internal", "Wintermute")
    
    # Try DeFiLlama
    protocol = find_defillama_protocol(name)
    if protocol is not None:
        category = protocol.get("category", "DeFi")
        return ("DeFi", category)
    
    # Fallback to non DeFi heuristics
    return classify_non_defi(name)


In [75]:
# Apply classification to from and to entities
df["from_entity_group"], df["from_entity_type"] = zip(*df["from_entity"].map(classify_entity))
df["to_entity_group"], df["to_entity_type"] = zip(*df["to_entity"].map(classify_entity))

df[["from_entity", "from_entity_group", "from_entity_type"]].head(10)


from_entity from_entity_group from_entity_type
0            Camelot              DeFi             Dexs
1            Uniswap              DeFi             Dexs
2  Aerodrome Finance              DeFi             Dexs
3         Wintermute          Internal       Wintermute
4            Uniswap              DeFi             Dexs
5         Wintermute          Internal       Wintermute
6            Camelot              DeFi             Dexs
7        PancakeSwap              DeFi             Dexs
8            Uniswap              DeFi             Dexs
9        PancakeSwap              DeFi             Dexs

In [76]:
# Quick overview of entity groups
df["from_entity_group"].value_counts(dropna=False), df["to_entity_group"].value_counts(dropna=False)


(from_entity_group
 Internal    231737
 DeFi        144246
 Unknown      60966
 Non-DeFi        51
 Name: count, dtype: int64,
 to_entity_group
 DeFi        192505
 Internal    184897
 Unknown      59567
 Non-DeFi        31
 Name: count, dtype: int64)

## 5. Counterparty extraction relative to Wintermute

We are interested in transactions where Wintermute appears as either the sender or receiver.

For each such transaction we define the counterparty as the entity on the opposite side.


In [77]:
def get_counterparty(row):
    """
    Return the counterparty entity relative to Wintermute.

    If Wintermute is the sender, the counterparty is the receiver, and vice versa.
    If Wintermute is not involved, return NaN.
    """
    if row["from_entity"] == "Wintermute":
        return row["to_entity"]
    if row["to_entity"] == "Wintermute":
        return row["from_entity"]
    return np.nan

df["counterparty_entity"] = df.apply(get_counterparty, axis=1)
df["counterparty_group"], df["counterparty_type"] = zip(*df["counterparty_entity"].map(classify_entity))


In [78]:
# Keep only rows where Wintermute is involved
df_wm = df[~df["counterparty_entity"].isna()].copy()
df_wm.shape


(375698, 18)

In [79]:
# Summary of counterparties: group, type, number of transactions, and total USD volume
counterparty_summary = (
    df_wm.groupby("counterparty_entity")
    .agg(
        counterparty_group=("counterparty_group", "first"),
        counterparty_type=("counterparty_type", "first"),
        n_txs=("tx_hash", "count"),
        volume_usd=("usd", "sum")
    )
    .sort_values("volume_usd", ascending=False)
)

counterparty_summary.head(15)


counterparty_group counterparty_type  n_txs    volume_usd
counterparty_entity                                                                
Uniswap                                 DeFi              Dexs  51477  3.573379e+08
Binance                                 DeFi               CEX    435  2.731336e+08
Wintermute                          Internal        Wintermute    278  1.466858e+08
Aerodrome Finance                       DeFi              Dexs   9002  1.116319e+08
Coinbase                                DeFi            Bridge    114  1.099160e+08
Orca                                    DeFi         Launchpad  84105  8.665894e+07
CoW Protocol                            DeFi             Yield   2155  6.933769e+07
Meteora (Prev. Mercurial)            Unknown           Unknown  31702  6.704490e+07
Fluid (Instadapp)                    Unknown           Unknown  13933  5.108056e+07
Kraken                                  DeFi               CEX     80  4.711274e+07
PancakeSwap                             DeFi              Dexs  21608  4.628817e+07
Rizzolver (Wintermute)               Unknown           Unknown    818  3.218466e+07
Raydium                                 DeFi              Dexs  82780  2.121679e+07
Bybit                                   DeFi               CEX     97  1.989914e+07
Bullish.com                         Non-DeFi               CEX     14  1.346026e+07

In [80]:
# Count of counterparties by group
counterparty_summary.groupby("counterparty_group")["n_txs"].sum(), counterparty_summary.groupby("counterparty_group").size()


(counterparty_group
 DeFi        324192
 Internal       278
 Non-DeFi        75
 Unknown      51153
 Name: n_txs, dtype: int64,
 counterparty_group
 DeFi        44
 Internal     1
 Non-DeFi    29
 Unknown     10
 dtype: int64)

## 6. DeFi vs Non DeFi subsets

We now build separate subsets for DeFi and non DeFi counterparties and compute high level statistics.


In [81]:
df_defi = df_wm[df_wm["counterparty_group"] == "DeFi"].copy()
df_non_defi = df_wm[df_wm["counterparty_group"] != "DeFi"].copy()

len(df_defi), len(df_non_defi)


(324192, 51506)

In [82]:
total_volume = df_wm["usd"].sum()
defi_volume = df_defi["usd"].sum()
non_defi_volume = df_non_defi["usd"].sum()

defi_share = defi_volume / total_volume * 100 if total_volume else 0
non_defi_share = non_defi_volume / total_volume * 100 if total_volume else 0

total_volume, defi_volume, non_defi_volume, defi_share, non_defi_share


(1527431163.8353603,
 1207774496.7734697,
 319656667.06188995,
 79.0722701860268,
 20.927729813973162)

`total_volume` is the total USD volume of Wintermute related transfers in the dataset.  
`defi_share` and `non_defi_share` give the percentage split between DeFi counterparties and everything else.


## 7. Token analysis for DeFi interactions


In [83]:
token_stats_defi = (
    df_defi.groupby("token")
    .agg(
        n_txs=("tx_hash", "count"),
        volume_token=("value", "sum"),
        volume_usd=("usd", "sum")
    )
    .sort_values("volume_usd", ascending=False)
)

token_stats_defi.head(15)


n_txs  volume_token    volume_usd
token                                   
USDC   84957  3.849293e+08  3.849295e+08
WETH   40150  1.496168e+05  2.359892e+08
ETH      290  9.103396e+04  1.442448e+08
USDT   17090  1.120104e+08  1.120047e+08
cbBTC   8088  8.586924e+02  6.847982e+07
WSOL   85186  5.095248e+05  5.610163e+07
SOL    48437  4.686030e+05  5.161631e+07
WBTC    9247  5.315434e+02  4.237113e+07
BTCB     945  2.576847e+02  2.046320e+07
WBNB    2798  1.825689e+04  1.022826e+07
TRUMP     26  9.731640e+05  7.636806e+06
AAVE     271  4.972258e+04  6.585501e+06
BNB       37  1.125028e+04  6.303969e+06
ARB     5351  1.609741e+07  4.429804e+06
LINK     223  3.184898e+05  3.705742e+06

We will visualize the top tokens by traded USD volume among DeFi counterparties.


## 8. Chain analysis for DeFi interactions


In [84]:
chain_stats_defi = (
    df_defi.groupby("chain")
    .agg(
        n_txs=("tx_hash", "count"),
        volume_usd=("usd", "sum")
    )
    .sort_values("volume_usd", ascending=False)
)

chain_stats_defi


n_txs    volume_usd
chain                             
ethereum       17857  7.276684e+08
solana        222127  1.959911e+08
base           19609  1.633041e+08
bsc             7484  5.896414e+07
arbitrum_one   53717  5.200757e+07
optimism        3388  9.380619e+06
avalanche          6  2.139753e+05
polygon            2  1.510000e+05
flare              2  9.364503e+04

## 9. Protocol and platform analysis for DeFi interactions


In [85]:
platform_stats_defi = (
    df_defi.groupby("counterparty_entity")
    .agg(
        counterparty_type=("counterparty_type", "first"),
        n_txs=("tx_hash", "count"),
        volume_usd=("usd", "sum")
    )
    .sort_values("volume_usd", ascending=False)
)

platform_stats_defi.head(15)


counterparty_type  n_txs    volume_usd
counterparty_entity                                       
Uniswap                          Dexs  51477  3.573379e+08
Binance                           CEX    435  2.731336e+08
Aerodrome Finance                Dexs   9002  1.116319e+08
Coinbase                       Bridge    114  1.099160e+08
Orca                        Launchpad  84105  8.665894e+07
CoW Protocol                    Yield   2155  6.933769e+07
Kraken                            CEX     80  4.711274e+07
PancakeSwap                      Dexs  21608  4.628817e+07
Raydium                          Dexs  82780  2.121679e+07
Bybit                             CEX     97  1.989914e+07
Gate.io                           CEX     50  1.203993e+07
OKX                               CEX     72  8.542148e+06
Phoenix                          Dexs   6266  8.196686e+06
Crypto.com             Liquid Staking     17  7.410505e+06
Velodrome Finance                Dexs   2346  6.221103e+06

## 10. Temporal analysis

We study how DeFi trading volume evolves over time within the sample day.


In [86]:
df_defi_ts = df_defi.sort_values("timestamp").set_index("timestamp")

hourly = df_defi_ts.resample("1H").agg(
    n_txs=("tx_hash", "count"),
    volume_usd=("usd", "sum")
).reset_index()

hourly.head()


timestamp  n_txs    volume_usd
0 2025-04-08 01:00:00+00:00  23819  6.302480e+07
1 2025-04-08 02:00:00+00:00  40428  1.836137e+08
2 2025-04-08 03:00:00+00:00  25817  8.307386e+07
3 2025-04-08 04:00:00+00:00  24169  1.222088e+08
4 2025-04-08 05:00:00+00:00  25986  7.044786e+07

## 11. Visualizations with Plotly

This section creates interactive charts for use in the written report.


In [95]:
# Top 10 DeFi tokens by USD volume
top_tokens = token_stats_defi.head(10).reset_index()

fig_tokens = px.bar(
    top_tokens,
    x="token",
    y="volume_usd",
    title="Top 10 DeFi tokens by USD volume",
    hover_data={"n_txs": True, "volume_token": True, "volume_usd": ":,.0f"},
)
fig_tokens.update_layout(
    xaxis_title="Token",
    yaxis_title="Volume (USD)",
)
fig_tokens.show()


In [96]:
# Top 10 DeFi counterparties by USD volume
top_platforms = platform_stats_defi.head(10).reset_index()

fig_platforms = px.bar(
    top_platforms,
    x="counterparty_entity",
    y="volume_usd",
    title="Top 10 DeFi counterparties by USD volume",
    hover_data={"n_txs": True, "counterparty_type": True, "volume_usd": ":,.0f"},
)
fig_platforms.update_layout(
    xaxis_title="DeFi platform",
    yaxis_title="Volume (USD)",
    xaxis_tickangle=-40,
)
fig_platforms.show()


In [89]:
# DeFi volume by chain
chain_plot = chain_stats_defi.reset_index()

fig_chains = px.bar(
    chain_plot,
    x="chain",
    y="volume_usd",
    title="DeFi volume by chain",
    hover_data={"n_txs": True, "volume_usd": ":,.0f"},
)
fig_chains.update_layout(
    xaxis_title="Chain",
    yaxis_title="Volume (USD)",
)
fig_chains.show()


In [90]:
# Hourly DeFi volume (USD)
fig_hourly = px.line(
    hourly,
    x="timestamp",
    y="volume_usd",
    title="Hourly DeFi volume (USD)",
    markers=True,
)
fig_hourly.update_layout(
    xaxis_title="Time (UTC)",
    yaxis_title="Volume (USD)",
)
fig_hourly.show()


In [101]:
# === Clean and professional histogram of DeFi trade sizes ===

import numpy as np
import plotly.express as px

# Filter positive values
df_defi_nonzero = df_defi[df_defi["usd"] > 0].copy()

# Log10 transform
df_defi_nonzero["log_usd"] = np.log10(df_defi_nonzero["usd"])

# Build histogram
fig = px.histogram(
    df_defi_nonzero,
    x="log_usd",
    nbins=70,
    title="Distribution of DeFi trade sizes (log10 scale of USD)",
)

# Nice readable ticks corresponding to real dollar amounts
tick_vals = [0, 1, 2, 3, 4, 5, 6, 7]
tick_text = ["$1", "$10", "$100", "$1k", "$10k", "$100k", "$1M", "$10M"]

fig.update_layout(
    xaxis=dict(
        tickmode="array",
        tickvals=tick_vals,
        ticktext=tick_text,
        title="Trade size (USD, log scale)",
    ),
    yaxis_title="Frequency",
)

fig.show()


In [108]:
# === Build DeFi Chain x Token volume matrix ===

# Group by chain and token
chain_token = df_defi.groupby(["chain", "token"])["usd"].sum().reset_index()

# Keep only tokens that matter (top 5 or 6 tokens)
top_tokens = (
    df_defi.groupby("token")["usd"].sum()
    .sort_values(ascending=False)
    .head(6)
    .index.tolist()
)

chain_token = chain_token[chain_token["token"].isin(top_tokens)]

# Pivot into heatmap matrix
heatmap_data = chain_token.pivot_table(
    index="chain",
    columns="token",
    values="usd",
    fill_value=0
)

heatmap_data


token                  ETH          USDC          USDT          WETH          WSOL         cbBTC
chain                                                                                           
arbitrum_one  7.035912e+06  1.459987e+07  4.572693e+06  1.629820e+07  0.000000e+00  0.000000e+00
base          6.311019e+06  6.556387e+07  0.000000e+00  4.430891e+07  0.000000e+00  4.226908e+07
bsc           5.047537e+05  0.000000e+00  1.903617e+07  0.000000e+00  0.000000e+00  0.000000e+00
ethereum      1.299774e+08  2.535887e+08  8.165971e+07  1.680671e+08  0.000000e+00  1.687353e+07
optimism      4.156461e+05  2.906283e+06  5.570195e+03  3.326597e+06  0.000000e+00  0.000000e+00
polygon       0.000000e+00  1.510000e+05  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00
solana        0.000000e+00  4.811973e+07  6.730550e+06  3.988344e+06  5.610163e+07  9.337211e+06

In [112]:

# Build chain × token volume table
chain_token = (
    df_defi.groupby(["chain", "token"])["usd"]
    .sum()
    .reset_index()
)

# Top N tokens by DeFi volume
top_tokens = (
    df_defi.groupby("token")["usd"]
    .sum()
    .sort_values(ascending=False)
    .head(5)          
    .index.tolist()
)

chain_token = chain_token[chain_token["token"].isin(top_tokens)]

heatmap_data = chain_token.pivot_table(
    index="chain",
    columns="token",
    values="usd",
    fill_value=0
)

fig = px.imshow(
    heatmap_data,
    labels=dict(x="Token", y="Chain", color="Volume (USD)"),
    x=heatmap_data.columns,
    y=heatmap_data.index,
    color_continuous_scale="Plasma",
    aspect=1  
)

fig.update_layout(
    title="DeFi volume by chain and top tokens",
    width=650,
    height=700,
    margin=dict(l=80, r=80, t=80, b=80),
    font=dict(size=16),
)

fig.update_xaxes(tickfont=dict(size=13))
fig.update_yaxes(tickfont=dict(size=13))

fig.show()


## 12. Optional: chain to platform Sankey diagram

This gives a coarse visual of how volume is distributed from chains to DeFi platforms.


In [93]:
# Aggregate volume by chain and platform
chain_platform = (
    df_defi.groupby(["chain", "counterparty_entity"])["usd"]
    .sum()
    .reset_index()
)

# Keep only the top platforms by volume for readability
top_platform_names = (
    chain_platform.groupby("counterparty_entity")["usd"]
    .sum()
    .sort_values(ascending=False)
    .head(8)
    .index
)

chain_platform_small = chain_platform[chain_platform["counterparty_entity"].isin(top_platform_names)]

# Build node list
chains = chain_platform_small["chain"].unique().tolist()
platforms = chain_platform_small["counterparty_entity"].unique().tolist()
nodes = chains + platforms
node_indices = {name: i for i, name in enumerate(nodes)}

source = [node_indices[c] for c in chain_platform_small["chain"]]
target = [node_indices[p] for p in chain_platform_small["counterparty_entity"]]
value = chain_platform_small["usd"].tolist()

fig_sankey = go.Figure(
    data=[
        go.Sankey(
            node=dict(
                label=nodes,
            ),
            link=dict(
                source=source,
                target=target,
                value=value,
            ),
        )
    ]
)

fig_sankey.update_layout(title_text="DeFi volume flow: chain to platform", font_size=12)
fig_sankey.show()


## 13. Export tables for the report

We save the key summary tables so they can be used in the written Google Doc or shared as CSV files.


In [94]:
counterparty_summary.to_csv("counterparty_summary.csv")
token_stats_defi.to_csv("defi_token_stats.csv")
chain_stats_defi.to_csv("defi_chain_stats.csv")
platform_stats_defi.to_csv("defi_platform_stats.csv")

print("Exported summary CSV files.")


Exported summary CSV files.


## 14. Conclusion

At this point, the notebook has:

- Loaded and inspected the Wintermute transfer dataset  
- Collected and classified counterparties using DeFiLlama and heuristic rules  
- Built a DeFi only subset of Wintermute interactions  
- Analyzed traded tokens, chains, and DeFi platforms  
- Studied hourly trading patterns  
- Produced professional visualizations suitable for inclusion in a report  
- Exported summary tables for documentation

You can now link this notebook in GitHub and use the figures and tables inside your Google Doc summary.
